In [1]:
import pandas as pd 
import datetime

import numpy as np
import chart_studio.plotly as py 
import seaborn as sns
import plotly.express as px
import cufflinks as cf
%matplotlib inline

import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected = True)
cf.go_offline()

In [2]:
pd.set_option('display.max_columns', None)

df = pd.read_excel('owid-covid-data.xlsx')


### Adding Year, Month, Day Column 

In [3]:
def get_year(x):
    return x.split('-')[0]
def get_month(x):
    return x.split('-')[1]
def get_day(x):
    return x.split('-')[2]


df['year'] = df['date'].apply(get_year)
df['month'] = df['date'].apply(get_month)
df['day'] = df['date'].apply(get_day)

df[['year','month','day']] = df[['year','month','day']].apply(pd.to_numeric)


In [4]:
df['fatality'] = df['total_deaths'] / df['total_cases'] 
df['fatality'] = df['fatality'] * 100
df = df.replace(np.nan,0)

In [5]:
df_PL = df[df['location'] == 'Poland']
df_PL

iso_code continent location        date  total_cases  new_cases  \
61846      POL    Europe   Poland  2020-03-04          1.0        1.0   
61847      POL    Europe   Poland  2020-03-05          1.0        0.0   
61848      POL    Europe   Poland  2020-03-06          5.0        4.0   
61849      POL    Europe   Poland  2020-03-07          5.0        0.0   
61850      POL    Europe   Poland  2020-03-08         11.0        6.0   
...        ...       ...      ...         ...          ...        ...   
62267      POL    Europe   Poland  2021-04-29    2785353.0     8426.0   
62268      POL    Europe   Poland  2021-04-30    2792142.0     6789.0   
62269      POL    Europe   Poland  2021-05-01    2798617.0     6475.0   
62270      POL    Europe   Poland  2021-05-02    2803233.0     4616.0   
62271      POL    Europe   Poland  2021-05-03    2805756.0     2523.0   

       new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  \
61846               0.000           0.0         0.0                0.000   
61847               0.000           0.0         0.0                0.000   
61848               0.000           0.0         0.0                0.000   
61849               0.000           0.0         0.0                0.000   
61850               0.000           0.0         0.0                0.000   
...                   ...           ...         ...                  ...   
62267            7728.143       67073.0       540.0              415.000   
62268            7145.714       67502.0       429.0              399.286   
62269            6712.143       67924.0       422.0              386.000   
62270            6339.571       68068.0       144.0              379.000   
62271            6204.714       68105.0        37.0              381.143   

       total_cases_per_million  new_cases_per_million  \
61846                    0.026                  0.026   
61847                    0.026                  0.000   
61848                    0.132                  0.106   
61849                    0.132                  0.000   
61850                    0.291                  0.159   
...                        ...                    ...   
62267                73595.848                222.636   
62268                73775.230                179.382   
62269                73946.316                171.085   
62270                74068.282                121.966   
62271                74134.946                 66.664   

       new_cases_smoothed_per_million  total_deaths_per_million  \
61846                           0.000                     0.000   
61847                           0.000                     0.000   
61848                           0.000                     0.000   
61849                           0.000                     0.000   
61850                           0.000                     0.000   
...                               ...                       ...   
62267                         204.196                  1772.233   
62268                         188.807                  1783.568   
62269                         177.351                  1794.718   
62270                         167.507                  1798.523   
62271                         163.944                  1799.501   

       new_deaths_per_million  new_deaths_smoothed_per_million  \
61846                   0.000                            0.000   
61847                   0.000                            0.000   
61848                   0.000                            0.000   
61849                   0.000                            0.000   
61850                   0.000                            0.000   
...                       ...                              ...   
62267                  14.268                           10.965   
62268                  11.335                           10.550   
62269                  11.150                           10.199   
62270                   3.805                           10.014   


In [6]:
fig = px.line(df_PL, x='date', y='fatality',
                title='Fatality During Covid-19 Outbreak in Poland',
                labels={'date': 'Date', 'fatality':'Fatality[%]'})
fig

In [7]:
fig = go.Figure()

fig.add_trace(go.Line(x=df_PL['date'], y=df_PL['new_cases_smoothed'],
                     name='New Cases'))
fig.add_trace(go.Line(x=df_PL['date'], y=df_PL['new_tests_smoothed'],
                     name='New Tests'))
fig.update_layout(title_text ='New Cases and New Tests in Poland During Covid-19 outbreak') 
fig.update_xaxes(title_text='Date')
fig.update_yaxes(title_text='Quantity')


C:\Users\01133904\Anaconda3\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




## Preapering Countries DF



In [8]:
countries_sum = df.groupby(['iso_code']).sum()
countries_mean = df.groupby(['iso_code']).mean()

countries_sum = countries_sum.drop(columns=['day', 'month', 'year','total_deaths','total_cases_per_million','total_deaths_per_million',
                                            'reproduction_rate','extreme_poverty','gdp_per_capita','aged_70_older','aged_65_older',
                                           'median_age','population_density','fatality','stringency_index','icu_patients','icu_patients_per_million',
                                           'population','handwashing_facilities','human_development_index','people_fully_vaccinated_per_hundred',
                                           'life_expectancy'])
iso = countries_sum.index.tolist()

countries_last = df.drop_duplicates(subset=['iso_code'],keep='last')
countries_last

iso_code continent     location        date  total_cases  new_cases  \
434         AFG      Asia  Afghanistan  2021-05-03      60300.0      178.0   
880    OWID_AFR         0       Africa  2021-05-03    4578852.0     7255.0   
1314        ALB    Europe      Albania  2021-05-03     131276.0       38.0   
1748        DZA    Africa      Algeria  2021-05-03     122717.0      195.0   
2176        AND    Europe      Andorra  2021-05-03      13295.0       13.0   
...         ...       ...          ...         ...          ...        ...   
84098       VNM      Asia      Vietnam  2021-05-03       2985.0       23.0   
84566  OWID_WRL         0        World  2021-05-03  153550816.0   680309.0   
84955       YEM      Asia        Yemen  2021-05-03       6363.0       22.0   
85367       ZMB    Africa       Zambia  2021-05-03      91722.0       29.0   
85777       ZWE    Africa     Zimbabwe  2021-05-03      38293.0       12.0   

       new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  \
434               183.571        2642.0         5.0                7.143   
880              9330.143      122554.0       257.0              303.857   
1314               95.714        2399.0         2.0                2.857   
1748              229.286        3280.0        10.0                9.000   
2176               30.286         127.0         0.0                0.429   
...                   ...           ...         ...                  ...   
84098              19.000          35.0         0.0                0.000   
84566          811202.000     3213594.0     11071.0            13290.000   
84955              25.714        1239.0         6.0                4.857   
85367              49.143        1253.0         0.0                0.714   
85777              27.286        1573.0         3.0                1.857   

       total_cases_per_million  new_cases_per_million  \
434                   1549.000                  4.573   
880                   3415.529                  5.412   
1314                 45616.791                 13.205   
1748                  2798.497                  4.447   
2176                172070.148                168.252   
...                        ...                    ...   
84098                   30.666                  0.236   
84566                19699.138                 87.277   
84955                  213.338                  0.738   
85367                 4989.242                  1.577   
85777                 2576.410                  0.807   

       new_cases_smoothed_per_million  total_deaths_per_million  \
434                             4.716                    67.868   
880                             6.960                    91.417   
1314                           33.260                   833.623   
1748                            5.229                    74.799   
2176                          391.972                  1643.694   
...                               ...                       ...   
84098                           0.195                     0.360   
84566                         104.070                   412.274   
84955                           0.862                    41.541   
85367                           2.673                    68.157   
85777                           1.836                   105.834   

       new_deaths_per_million  new_deaths_smoothed_per_million  \
434                     0.128                            0.183   
880                     0.192                            0.227   
1314                    0.695                            0.993   
1748                    0.228                            0.205   
2176                    0.000                            5.547   
...                       ...                              ...   
84098                   0.000                            0.000   
84566                   1.420                            1.705   
84955                   0.201                            0.163   
85367  

## Getting all columns

In [9]:
columns = df.columns
columns

Index(['iso_code', 'continent', 'location', 'date', 'total_cases', 'new_cases',
       'new_cases_smoothed', 'total_deaths', 'new_deaths',
       'new_deaths_smoothed', 'total_cases_per_million',
       'new_cases_per_million', 'new_cases_smoothed_per_million',
       'total_deaths_per_million', 'new_deaths_per_million',
       'new_deaths_smoothed_per_million', 'reproduction_rate', 'icu_patients',
       'icu_patients_per_million', 'hosp_patients',
       'hosp_patients_per_million', 'weekly_icu_admissions',
       'weekly_icu_admissions_per_million', 'weekly_hosp_admissions',
       'weekly_hosp_admissions_per_million', 'new_tests', 'total_tests',
       'total_tests_per_thousand', 'new_tests_per_thousand',
       'new_tests_smoothed', 'new_tests_smoothed_per_thousand',
       'positive_rate', 'tests_per_case', 'tests_units', 'total_vaccinations',
       'people_vaccinated', 'people_fully_vaccinated', 'new_vaccinations',
       'new_vaccinations_smoothed', 'total_vaccinations_per_hun

In [10]:
df_EU = df[df['continent'] == 'Europe']
df_EU = df_EU[~(df_EU.location.isin(["Andora", "Liechtendtein", "Luxembourg", "Vatican",'Guernsey', "Gibraltar","Faeroe Islands","Jersey"]))]

fig = px.line(df_EU, x='date', y='new_cases_smoothed', 
                    color='location')

fig

In [11]:
fig = px.bar(df_EU , x='location', y='total_cases', animation_frame='date',color='fatality',
            title='The course of a pandemic in Europe')
fig.show()

In [12]:
# Mapa świata

fig = go.Figure(data=go.Choropleth(
                locations=iso,
                z = countries_mean['fatality'],
                locationmode='ISO-3'))
fig.update_layout(title_text ='Mean fatality During Covid-19 outbreak') 
fig.update_layout(legend_title_text = "Fatality[%]")

In [26]:
countries_last.to_excel('countries_database.xlsx')

In [22]:
countries_last = countries_last[countries_last['new_cases']!=0]
countries_last = countries_last[countries_last['continent']!=0]

fig = px.sunburst(countries_last, path=['continent', 'location'], values='total_cases',
                  color='hospital_beds_per_thousand', hover_data=['iso_code'],
                 title='Distribution of all cases',
                 color_continuous_scale=["red", "yellow", "green"])
fig.show()

In [31]:
countries_plot = countries_last[countries_last['total_deaths'] != 0]

countries_plot

fig = px.sunburst(countries_plot, path=['continent', 'location'], values='total_deaths',
                  color='hospital_beds_per_thousand', hover_data=['iso_code'],
                 title='Distribution of all deaths',
                 color_continuous_scale=["red", "yellow", "green"])
fig.show()

In [33]:
fig = px.sunburst(countries_plot, path=['continent', 'location'], values='total_deaths',
                  color='cardiovasc_death_rate', hover_data=['iso_code'],
                 title='Distribution of all deaths',
                 color_continuous_scale=["red", "yellow", "green"])
fig.show()

### Corelations  

In [40]:
df_cov = countries_plot.cov()
df_cov
df_cov['total_deaths'].nlargest(15)

population                        3.726761e+12
total_cases                       2.026895e+11
total_deaths                      4.158088e+09
new_cases_smoothed                8.831398e+08
new_cases                         7.450974e+08
total_cases_per_million           4.725643e+08
gdp_per_capita                    1.707333e+08
total_deaths_per_million          1.574967e+07
new_deaths_smoothed               1.476017e+07
new_deaths                        1.015715e+07
new_cases_smoothed_per_million    9.046909e+05
female_smokers                    1.160103e+05
median_age                        1.141571e+05
aged_65_older                     7.503886e+04
life_expectancy                   6.133392e+04
Name: total_deaths, dtype: float64